In [ ]:
!pip install prophet dagshub scikit-learn pandas "numpy<2.0" mlflow pyarrow==14.0.1 neuralforecast

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.pipeline import Pipeline
import warnings
warnings.filterwarnings('ignore')

import mlflow
import mlflow.sklearn
import dagshub
import os

In [ ]:
os.environ['MLFLOW_TRACKING_USERNAME'] = 'nipkha21'
os.environ['MLFLOW_TRACKING_PASSWORD'] = '202fb8a4c58a90b0eb3598b1037498eb6fe9f593'

dagshub.init(repo_owner='TomC333', repo_name='ml-walmart-recruiting', mlflow=True)
mlflow.set_tracking_uri('https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow')

try:
    from neuralforecast import NeuralForecast
    from neuralforecast.models import DLinear
except ImportError:
    print("Installing neuralforecast...")
    import subprocess
    subprocess.check_call(["pip", "install", "neuralforecast"])
    from neuralforecast import NeuralForecast
    from neuralforecast.models import DLinear

import torch

print("Setup complete!")

❗❗❗ AUTHORIZATION REQUIRED ❗❗❗

Output()



Open the following link in your browser to authorize the client:
https://dagshub.com/login/oauth/authorize?state=6f8a8d5d-9b94-42e9-be20-cf38f5f83d9b&client_id=32b60ba385aa7cecf24046d8195a71c07dd345d9657977863b52e7748e0f0f28&middleman_request_id=76acfa9d2d5ded853c49047a011a2ff7a46777a54a3f533d27c0a3bccea4a618




Accessing as nipkha21

Initialized MLflow to track repo "TomC333/ml-walmart-recruiting"

Repository TomC333/ml-walmart-recruiting initialized!

Setup complete!


In [ ]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')

print(f"Train shape: {train.shape}")
print(f"Test shape: {test.shape}")

print("\nTrain data sample:")
print(train.head())
print(f"\nWeekly_Sales stats:")
print(train['Weekly_Sales'].describe())

train['Date'] = pd.to_datetime(train['Date'])
test['Date'] = pd.to_datetime(test['Date'])

print(f"\nDate Analysis:")
print(f"Training data date range: {train['Date'].min()} to {train['Date'].max()}")
print(f"Test data date range: {test['Date'].min()} to {test['Date'].max()}")
print(f"Gap between train and test: {(test['Date'].min() - train['Date'].max()).days} days")

print(f"\nData structure:")
print(f"Training: {train['Store'].nunique()} stores, {train['Dept'].nunique()} departments")
print(f"Test: {test['Store'].nunique()} stores, {test['Dept'].nunique()} departments")
print(f"Training series: {len(train.groupby(['Store', 'Dept']))}")
print(f"Test series: {len(test.groupby(['Store', 'Dept']))}")

train_series = set(zip(train['Store'], train['Dept']))
test_series = set(zip(test['Store'], test['Dept']))
common_series = train_series.intersection(test_series)
print(f"Common Store-Dept combinations: {len(common_series)}")
print(f"Test-only series: {len(test_series - train_series)}")
print(f"Train-only series: {len(train_series - test_series)}")

if len(test_series - train_series) > 0:
    print("WARNING: Test set contains Store-Dept combinations not seen in training!")

Train shape: (421570, 5)
Test shape: (115064, 4)

Train data sample:
   Store  Dept        Date  Weekly_Sales  IsHoliday
0      1     1  2010-02-05      24924.50      False
1      1     1  2010-02-12      46039.49       True
2      1     1  2010-02-19      41595.55      False
3      1     1  2010-02-26      19403.54      False
4      1     1  2010-03-05      21827.90      False

Weekly_Sales stats:
count    421570.000000
mean      15981.258123
std       22711.183519
min       -4988.940000
25%        2079.650000
50%        7612.030000
75%       20205.852500
max      693099.360000
Name: Weekly_Sales, dtype: float64

Date Analysis:
Training data date range: 2010-02-05 00:00:00 to 2012-10-26 00:00:00
Test data date range: 2012-11-02 00:00:00 to 2013-07-26 00:00:00
Gap between train and test: 7 days

Data structure:
Training: 45 stores, 81 departments
Test: 45 stores, 81 departments
Training series: 3331
Test series: 3169
Common Store-Dept combinations: 3158
Test-only series: 11
Train-only 

In [ ]:
class SimpleDLinearPreprocessor(BaseEstimator, TransformerMixin):

    def fit(self, X, y=None):
        return self

    def transform(self, X):
        df = X.copy()
        df['Date'] = pd.to_datetime(df['Date'])

        if 'Weekly_Sales' in df.columns:
            df['y'] = df['Weekly_Sales']
        else:
            df['y'] = 0.0

        df['unique_id'] = df['Dept'].astype(str) + '_' + df['Store'].astype(str)
        df = df.rename(columns={'Date': 'ds'})

        return df[['unique_id', 'ds', 'y', 'IsHoliday']]

In [ ]:
def split_sales_data(df: pd.DataFrame, split_date: pd.Timestamp = pd.Timestamp('2012-02-15')):
    df = df.copy()
    df['Date'] = pd.to_datetime(df['Date'])

    train_mask = df['Date'] < split_date
    test_mask = df['Date'] >= split_date

    df_train = df[train_mask].copy()
    df_test = df[test_mask].copy()

    return df_train, df_test

train_data, val_data = split_sales_data(train)

print(f"Training data: {train_data.shape[0]} rows")
print(f"Validation data: {val_data.shape[0]} rows")
print(f"Training period: {train_data['Date'].min()} to {train_data['Date'].max()}")
print(f"Validation period: {val_data['Date'].min()} to {val_data['Date'].max()}")


Training data: 311960 rows
Validation data: 109610 rows
Training period: 2010-02-05 00:00:00 to 2012-02-10 00:00:00
Validation period: 2012-02-17 00:00:00 to 2012-10-26 00:00:00


In [ ]:
preprocessor = SimpleDLinearPreprocessor()

train_df, val_df = split_sales_data(train)

train_df = preprocessor.fit_transform(train_df)
val_df = preprocessor.transform(val_df)

w_train = train_df["IsHoliday"].map({True: 5, False: 1}).values
w_val = val_df["IsHoliday"].map({True: 5, False: 1}).values
train_df = train_df.drop('IsHoliday', axis=1)
val_df = val_df.drop('IsHoliday', axis=1)

X_train = train_df.drop('y', axis=1)
y_train = train_df['y']
X_val = val_df.drop('y', axis=1)
y_val = val_df['y']

print(f"Processed training data shape: {train_df.shape}")
print(f"Processed validation data shape: {val_df.shape}")
print(f"Number of unique series: {train_df['unique_id'].nunique()}")

print(f"\nData quality check:")
print(f"Training data - NaN values: {train_df.isnull().sum().sum()}")
print(f"Validation data - NaN values: {val_df.isnull().sum().sum()}")
print(f"Training data - y stats: min={train_df['y'].min():.2f}, max={train_df['y'].max():.2f}, mean={train_df['y'].mean():.2f}")

Processed training data shape: (311960, 3)
Processed validation data shape: (109610, 3)
Number of unique series: 3309

Data quality check:
Training data - NaN values: 0
Validation data - NaN values: 0
Training data - y stats: min=-4988.94, max=693099.36, mean=16034.35


In [ ]:
def weighted_mae(y_true, y_pred, weights):
    mask = np.isfinite(y_true) & np.isfinite(y_pred) & np.isfinite(weights)
    if not mask.any() or weights[mask].sum() == 0:
        return np.nan

    y_true_clean = y_true[mask]
    y_pred_clean = y_pred[mask]
    weights_clean = weights[mask]

    return (weights_clean * np.abs(y_true_clean - y_pred_clean)).sum() / weights_clean.sum()

def calculate_metrics(y_true, y_pred, weights=None):
    if weights is None:
        weights = np.ones_like(y_true)

    metrics = {
        'WMAE': weighted_mae(y_true, y_pred, weights),
        'MAE': mean_absolute_error(y_true, y_pred),
        'RMSE': np.sqrt(mean_squared_error(y_true, y_pred)),
        'R2': r2_score(y_true, y_pred)
    }
    return metrics

def plot_predictions(y_true, y_pred, title="Predictions vs Actual", sample_size=5000):
    if len(y_true) > sample_size:
        indices = np.random.choice(len(y_true), sample_size, replace=False)
        y_true_sample = y_true[indices]
        y_pred_sample = y_pred[indices]
    else:
        y_true_sample = y_true
        y_pred_sample = y_pred

    plt.figure(figsize=(10, 6))
    plt.subplot(1, 2, 1)
    plt.scatter(y_true_sample, y_pred_sample, alpha=0.5, s=1)
    plt.plot([y_true_sample.min(), y_true_sample.max()],
             [y_true_sample.min(), y_true_sample.max()], 'r--', lw=2)
    plt.xlabel('Actual')
    plt.ylabel('Predicted')
    plt.title(f'{title} - Scatter Plot')

    plt.subplot(1, 2, 2)
    residuals = y_true_sample - y_pred_sample
    plt.scatter(y_pred_sample, residuals, alpha=0.5, s=1)
    plt.axhline(y=0, color='r', linestyle='--')
    plt.xlabel('Predicted')
    plt.ylabel('Residuals')
    plt.title('Residuals Plot')

    plt.tight_layout()
    return plt.gcf()

In [ ]:
class DLinearModel(BaseEstimator, TransformerMixin):

    def __init__(self,
                 input_size=52,
                 h=40,
                 max_steps=2000,
                 batch_size=64,
                 learning_rate=0.001,
                 random_seed=42):

        self.input_size = input_size
        self.h = h
        self.max_steps = max_steps
        self.batch_size = batch_size
        self.learning_rate = learning_rate
        self.random_seed = random_seed
        self.nf = None
        self.is_fitted = False

    def fit(self, X, y=None):
        if not self.is_fitted:
            if isinstance(X, pd.DataFrame) and 'y' in X.columns:
                df = X.copy()
            elif y is not None:
                df = X.copy()
                df['y'] = y
            else:
                raise ValueError("Either X should have 'y' column or y should be provided separately")

            df = df.sort_values(['unique_id', 'ds']).reset_index(drop=True)

            series_lengths = df.groupby('unique_id').size()
            min_length = series_lengths.min()
            print(f"Minimum series length: {min_length}")
            print(f"Input size requirement: {self.input_size}")

            device = "gpu" if torch.cuda.is_available() else "cpu"

            model = DLinear(
                input_size=self.input_size,
                h=self.h,
                max_steps=self.max_steps,
                batch_size=self.batch_size,
                random_seed=self.random_seed,
                accelerator=device,
                devices=1,
                logger=False,
                enable_progress_bar=True,
                enable_model_summary=False
            )

            self.nf = NeuralForecast(models=[model], freq='W-FRI')

            print(f"Fitting DLinear model with {df['unique_id'].nunique()} series...")
            print(f"Total data points: {len(df)}")
            print(f"Using parameters:")
            print(f"  input_size: {self.input_size}")
            print(f"  h: {self.h}")
            print(f"  max_steps: {self.max_steps}")
            print(f"  batch_size: {self.batch_size}")

            self.nf.fit(df)
            self.is_fitted = True

        return self

    def predict(self, X=None):
        if not self.is_fitted:
            raise ValueError("Model must be fitted before making predictions")

        if X is not None:
            if 'y' not in X.columns:
                X_with_y = X.copy()
                X_with_y['y'] = 0
            else:
                X_with_y = X.copy()

            real = pd.DataFrame({"unique_id": X_with_y["unique_id"], "ds": X_with_y["ds"], "y": X_with_y["y"]})
            preds = self.nf.predict()
            merged = real.merge(preds, on=["unique_id", "ds"], how="left").fillna(0)

            return merged
        else:
            return self.nf.predict()

def evaluate_model_performance(model, train_data, val_data, model_name="DLinear"):
    val_data_with_y = val_data.copy()
    val_data_with_y['y'] = y_val.values

    preds_df = model.predict(val_data_with_y)
    pred_col = preds_df.columns[-1]
    y_pred = preds_df[pred_col].values

    print(f"Evaluation summary:")
    print(f"  Total predictions: {len(y_pred)}")
    print(f"  Non-zero predictions: {(y_pred != 0).sum()}")
    print(f"  Prediction range: [{y_pred.min():.2f}, {y_pred.max():.2f}]")
    print(f"  Actual range: [{y_val.values.min():.2f}, {y_val.values.max():.2f}]")

    weights = w_val
    metrics = calculate_metrics(y_val.values, y_pred, weights)

    return metrics, y_val.values, y_pred

In [ ]:
print("\n" + "="*60)
print("TESTING DLINEAR WITH BASELINE PARAMETERS")
print("="*60)

baseline_params = {
    'input_size': 52,
    'h': 40,
    'max_steps': 2000,
    'batch_size': 64,
    'learning_rate': 0.001,
    'random_seed': 42
}

print(f"Using baseline parameters: {baseline_params}")

mlflow.set_experiment("DLINEAR_Training")

with mlflow.start_run(run_name="DLINEAR_Baseline"):

    mlflow.log_params(baseline_params)

    model = DLinearModel(**baseline_params)
    model.fit(train_df)

    metrics, y_true, y_pred = evaluate_model_performance(model, train_df, val_df)

    for metric, value in metrics.items():
        mlflow.log_metric(f"val_{metric}", value)

    print(f"\nValidation Metrics:")
    for metric, value in metrics.items():
        print(f"  {metric}: {value:.4f}")

    fig = plot_predictions(y_true, y_pred, "Validation Set - Baseline")
    mlflow.log_figure(fig, "validation_predictions.png")
    plt.close(fig)

    # mlflow.sklearn.log_model(model, "model")

    baseline_wmae = metrics['WMAE']


2025/08/03 00:37:22 INFO mlflow.tracking.fluent: Experiment with name 'DLINEAR_Training' does not exist. Creating a new experiment.



TESTING DLINEAR WITH BASELINE PARAMETERS
Using baseline parameters: {'input_size': 52, 'h': 40, 'max_steps': 2000, 'batch_size': 64, 'learning_rate': 0.001, 'random_seed': 42}


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 40
  max_steps: 2000
  batch_size: 64


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Predicting: |          | 0/? [00:00<?, ?it/s]

Evaluation summary:
  Total predictions: 109610
  Non-zero predictions: 109283
  Prediction range: [-21012.77, 220125.09]
  Actual range: [-1699.00, 224917.94]

Validation Metrics:
  WMAE: 1813.7293
  MAE: 1795.0515
  RMSE: 3839.0898
  R2: 0.9698


2025/08/03 00:38:31 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.


🏃 View run DLINEAR_Baseline at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/23/runs/9fdede1e81ff42ed95852f2848751aba
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/23


RestException: INTERNAL_ERROR: Response: {'error': 'unsupported endpoint, please contact support@dagshub.com'}

In [ ]:
baseline_wmae = metrics['WMAE']

In [ ]:
print("\n" + "="*60)
print("SYSTEMATIC HYPERPARAMETER TUNING")
print("="*60)

def run_experiment(params, experiment_name, run_name):
    mlflow.set_experiment(experiment_name)

    with mlflow.start_run(run_name=run_name):
        mlflow.log_params(params)

        model = DLinearModel(**params)
        model.fit(X_train, y_train)

        val_data_with_y = X_val.copy()
        val_data_with_y['y'] = y_val.values

        preds_df = model.predict(val_data_with_y)
        pred_col = preds_df.columns[-1]
        y_pred = preds_df[pred_col].values

        weights = w_val
        metrics = calculate_metrics(y_val.values, y_pred, weights)

        for metric, value in metrics.items():
            mlflow.log_metric(f"val_{metric}", value)

        print(f"{run_name}: WMAE = {metrics['WMAE']:.2f}")

        return metrics['WMAE'], model

best_val_wmae = float('inf')
best_params_found = baseline_params.copy()
best_model = None


SYSTEMATIC HYPERPARAMETER TUNING


In [ ]:
print("\n1. Testing Input Sizes...")
input_sizes = [26, 52, 78, 104]

for input_size in input_sizes:
    params = baseline_params.copy()
    params['input_size'] = input_size

    val_wmae, model = run_experiment(
        params,
        "DLINEAR_Hyperparameter_Tuning",
        f"InputSize_{input_size}"
    )

    if val_wmae < best_val_wmae:
        best_val_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")

2025/08/03 00:39:16 INFO mlflow.tracking.fluent: Experiment with name 'DLINEAR_Hyperparameter_Tuning' does not exist. Creating a new experiment.



1. Testing Input Sizes...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 26
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 26
  h: 40
  max_steps: 2000
  batch_size: 64


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=2000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

InputSize_104: WMAE = 16677.23
🏃 View run InputSize_104 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/233bdb91a7764779becfa54afcae4377
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24


In [ ]:
print("\n2. Testing Horizons...")
horizons = [24, 32, 40, 48]

for h in horizons:
    params = best_params_found.copy()
    params['h'] = h

    val_wmae, model = run_experiment(
        params,
        "DLINEAR_Hyperparameter_Tuning",
        f"Horizon_{h}"
    )

    if val_wmae < best_val_wmae:
        best_val_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


2. Testing Horizons...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 24
  max_steps: 2000
  batch_size: 64


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=2000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

Horizon_48: WMAE = 1827.03
🏃 View run Horizon_48 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/d552c43572dd4ac9a9d57c5138ee5b13
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24


In [ ]:
print("\n3. Testing Learning Rates...")
learning_rates = [0.0005, 0.001, 0.002, 0.005]

for lr in learning_rates:
    params = best_params_found.copy()
    params['learning_rate'] = lr

    val_wmae, model = run_experiment(
        params,
        "DLINEAR_Hyperparameter_Tuning",
        f"LR_{lr}"
    )

    if val_wmae < best_val_wmae:
        best_val_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


3. Testing Learning Rates...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 40
  max_steps: 2000
  batch_size: 64


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=2000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

LR_0.005: WMAE = 1813.73
🏃 View run LR_0.005 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/9eeff74df44e4cb2ba0165b2fe052f3e
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24


In [ ]:
print("\n4. Testing Batch Sizes...")
batch_sizes = [32, 64, 128, 256]

for batch_size in batch_sizes:
    params = best_params_found.copy()
    params['batch_size'] = batch_size

    val_wmae, model = run_experiment(
        params,
        "DLINEAR_Hyperparameter_Tuning",
        f"BatchSize_{batch_size}"
    )

    if val_wmae < best_val_wmae:
        best_val_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")


4. Testing Batch Sizes...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 40
  max_steps: 2000
  batch_size: 32


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=2000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

BatchSize_256: WMAE = 1798.58
🏃 View run BatchSize_256 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/06acc0f556fd4b85a7d30abed46ea0c4
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24


In [ ]:
print("\n5. Testing Training Steps...")
max_steps_options = [1000, 1500, 2000, 2500, 3000]

for max_steps in max_steps_options:
    params = best_params_found.copy()
    params['max_steps'] = max_steps

    val_wmae, model = run_experiment(
        params,
        "DLINEAR_Hyperparameter_Tuning",
        f"Steps_{max_steps}"
    )

    if val_wmae < best_val_wmae:
        best_val_wmae = val_wmae
        best_params_found = params.copy()
        best_model = model
        print(f"  → New best! WMAE: {val_wmae:.2f}")



5. Testing Training Steps...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3309 series...
Total data points: 311960
Using parameters:
  input_size: 52
  h: 40
  max_steps: 1000
  batch_size: 128


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_steps=3000` reached.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

Steps_3000: WMAE = 1685.32
🏃 View run Steps_3000 at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/61b540be0031413d8c03753f9904aa80
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24
  → New best! WMAE: 1685.32


In [ ]:
print("\n" + "="*60)
print("HYPERPARAMETER TUNING RESULTS")
print("="*60)
print(f"Best Validation WMAE: {best_val_wmae:.4f}")
print(f"Improvement over baseline: {((baseline_wmae - best_val_wmae) / baseline_wmae * 100):.2f}%")
print(f"\nBest Parameters:")
for param, value in best_params_found.items():
    print(f"  {param}: {value}")


HYPERPARAMETER TUNING RESULTS
Best Validation WMAE: 1685.3183
Improvement over baseline: 7.08%

Best Parameters:
  input_size: 52
  h: 40
  max_steps: 3000
  batch_size: 128
  learning_rate: 0.001
  random_seed: 42


In [ ]:
print(f"\nGenerating final submission with best parameters...")

full_train_df = preprocessor.transform(train)
w_full = full_train_df["IsHoliday"].map({True: 5, False: 1}).values
full_train_df = full_train_df.drop('IsHoliday', axis=1)

final_model = DLinearModel(**best_params_found)
final_model.fit(full_train_df)

test_df = preprocessor.transform(test)
test_df = test_df.drop('IsHoliday', axis=1)

def generate_kaggle_submission(model, test_features, original_test):
    preds_df = model.predict(test_features)
    y_pred = preds_df.iloc[:, -1].values

    submission = pd.DataFrame({
        "Id": original_test["Store"].astype(str) + "_" + original_test["Dept"].astype(str) + "_" + original_test["Date"].astype(str),
        "Weekly_Sales": y_pred
    })

    return submission

final_submission = generate_kaggle_submission(final_model, test_df, test)
final_submission.to_csv('dlinear_best_submission.csv', index=False)

print(f"\nSubmission generated successfully!")
print(f"Submission shape: {final_submission.shape}")
print("Submission sample:")
print(final_submission.head(10))
print(f"Submission stats:")
print(f"  Min: {final_submission['Weekly_Sales'].min():.2f}")
print(f"  Max: {final_submission['Weekly_Sales'].max():.2f}")
print(f"  Mean: {final_submission['Weekly_Sales'].mean():.2f}")
print(f"  Non-zero predictions: {(final_submission['Weekly_Sales'] != 0).sum()} / {len(final_submission)}")

with mlflow.start_run(run_name="DLINEAR_Final_Model"):
    mlflow.log_params(best_params_found)
    mlflow.sklearn.log_model(
        final_model,
        "final_model",
        registered_model_name="DLINEAR_Walmart_Sales"
    )
    mlflow.log_artifact('dlinear_best_submission.csv')
    print("Final model registered in MLflow Model Registry as 'DLINEAR_Walmart_Sales'")

print("\n" + "="*60)
print("EXPERIMENT COMPLETE")
print("="*60)
print(f"Best Validation WMAE: {best_val_wmae:.4f}")
print(f"Best Parameters:")
for param, value in best_params_found.items():
    print(f"  {param}: {value}")
print(f"Submission file: dlinear_best_submission.csv")
print(f"Model registered: DLINEAR_Walmart_Sales")
print("="*60)


Generating final submission with best parameters...


INFO:lightning_fabric.utilities.seed:Seed set to 42
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs


Minimum series length: 1
Input size requirement: 52
Fitting DLinear model with 3331 series...
Total data points: 421570
Using parameters:
  input_size: 52
  h: 40
  max_steps: 3000
  batch_size: 128


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

...

Predicting: |          | 0/? [00:00<?, ?it/s]


Submission generated successfully!
Submission shape: (115064, 2)
Submission sample:
               Id  Weekly_Sales
0  1_1_2012-11-02  31686.281250
1  1_1_2012-11-09  23806.705078
2  1_1_2012-11-16  20593.066406
3  1_1_2012-11-23  23404.542969
4  1_1_2012-11-30  26600.333984
5  1_1_2012-12-07  29315.394531
6  1_1_2012-12-14  33788.621094
7  1_1_2012-12-21  33973.574219
8  1_1_2012-12-28  25165.974609
9  1_1_2013-01-04  21098.703125
Submission stats:
  Min: -394.40
  Max: 235711.02
  Mean: 16357.26
  Non-zero predictions: 114718 / 115064


2025/08/03 01:11:59 WARNING mlflow.models.model: `artifact_path` is deprecated. Please use `name` instead.


🏃 View run DLINEAR_Final_Model at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24/runs/1c186fb65b3b4f1486d78a3f4a2b638f
🧪 View experiment at: https://dagshub.com/TomC333/ml-walmart-recruiting.mlflow/#/experiments/24


RestException: INTERNAL_ERROR: Response: {'error': 'unsupported endpoint, please contact support@dagshub.com'}